# Ensemble for Binary Classification
---
This notebook contains the solution I made for the Kaggle competition "Binary Classification with a Tabular Credit Card Fraud Dataset" from the Playground Series - Season 3, Episode 4. The data used for it was all downloaded from Kaggle, the fist 2 files directly from the competition and the third one being the origanl dataset from which the other 2 and the competition on itself was based. The feature engineering done was based on several of the discussions found within the competition and the idea of using an ensemble was also taken from an explanation for one of the top solutions. 

In [1]:
import pandas as pd
import seaborn as sns
import matplotlib.pyplot as plt
import sklearn as sk
import numpy as np
import xgboost as xgb
import optuna
import lightgbm as lgb

from sklearn.utils import resample
from sklearn.feature_selection import SelectKBest, f_classif
from sklearn.model_selection import train_test_split
from imblearn.over_sampling import SMOTE
from sklearn.metrics import roc_auc_score
from sklearn.model_selection import StratifiedKFold
from sklearn.metrics import precision_recall_curve, auc
from sklearn.ensemble import RandomForestClassifier
from sklearn.model_selection import cross_val_score
from catboost import CatBoostClassifier
from sklearn.metrics import average_precision_score
from sklearn.preprocessing import StandardScaler
from sklearn.metrics import log_loss
from sklearn.model_selection import StratifiedShuffleSplit, RandomizedSearchCV
from xgboost import XGBClassifier
from sklearn.model_selection import KFold
from sklearn.ensemble import VotingClassifier

C:\Users\logan\anaconda3\lib\site-packages\dask\dataframe\utils.py:369: FutureWarning: pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.
  _numeric_index_types = (pd.Int64Index, pd.Float64Index, pd.UInt64Index)
C:\Users\logan\anaconda3\lib\site-packages\dask\dataframe\utils.py:369: FutureWarning: pandas.Float64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.
  _numeric_index_types = (pd.Int64Index, pd.Float64Index, pd.UInt64Index)
C:\Users\logan\anaconda3\lib\site-packages\dask\dataframe\utils.py:369: FutureWarning: pandas.UInt64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.
  _numeric_index_types = (pd.Int64Index, pd.Float64Index, pd.UInt64Index)


---
Using the original dataset with the intention of adding only the positive class.

In [2]:
test = pd.read_csv (r'C:\Users\logan\Desktop\CC Fraud files\test.csv')
just_train = pd.read_csv (r'C:\Users\logan\Desktop\CC Fraud files\train.csv')
original = pd.read_csv (r'C:\Users\logan\Desktop\CC Fraud files\creditcard.csv')

In [3]:
just_train0 = just_train.drop('id', axis=1)
original_1 = original[original['Class'] == 1]

train = pd.concat([just_train0, original_1], axis=0, ignore_index=True)


In [4]:
train['Class'].value_counts()

0    218660
1       961
Name: Class, dtype: int64

With this quick check, it is assured that the training dataset is extremely imbalanced between classes.


In [5]:
#Adding feature to the training and test datasets also dropping some features
train['V20_div_Amount'] = train.V20 / (train.Amount + 1e-6)
test['V20_div_Amount'] = test.V20 / (test.Amount + 1e-6)

dropped_df = train.drop(['Time'], axis=1)
test_df = test.drop(['id','Time'], axis=1)

After having all the desired features, everything gets scaled

In [6]:
# define columns to scale and exclude column named 'Class'
columns_to_scale = [col for col in dropped_df.columns if col != 'Class']

# initialize scaler and fit_transform on selected columns
scaler = StandardScaler()
scaler.fit(dropped_df[columns_to_scale])
inscaler = scaler.transform(dropped_df[columns_to_scale])

# create a new DataFrame with scaled columns
scaled_df = pd.DataFrame(inscaler, columns=columns_to_scale)

# add the 'Class' column to the scaled DataFrame
#scaled_df.drop('Class', axis=1, inplace=True)
scaled_df['Class'] = dropped_df['Class']

# assign scaled DataFrame to train_df


In [8]:
#Check that Class was switched correctly and not scaled
scaled_df['Class'].value_counts()

0    218660
1       961
Name: Class, dtype: int64

In order to treat the extreme class imbalance, several techniques were applied. Using an article from Google as refernce, it was opted to first do a downsample of the majority class going from a 227:1 ratio to a 5:1 and then applying higher class weights to the minority class while training the models.

In [9]:
# Separate majority and minority classes
majority_class = scaled_df[scaled_df['Class']==0]
minority_class = scaled_df[scaled_df['Class']==1]

# Downsample the majority class
downsampled_majority = resample(majority_class, 
                                replace=False, # sample without replacement
                                n_samples=len(minority_class)*5, # to achieve 5:1 ratio
                                random_state=42) # reproducible results

# Combine the minority class with the downsampled majority class
downsampled_df = pd.concat([downsampled_majority, minority_class])

# Shuffle the dataset
shuffled_df = downsampled_df.sample(frac=1, random_state=42)

In [10]:
train_df = shuffled_df

In [11]:
X = train_df.drop('Class', axis=1)
y = train_df['Class']

In [12]:
train_df['Class'].value_counts()

0    4805
1     961
Name: Class, dtype: int64

# Part 1
---
Cross-validation with stratifiedKfold 10 splits on Lgbmclassifier with Optuna

In [13]:
#weigh classes on lgm
class_weights_lgbm = {0: 1, 1: 55}


In [14]:
def objective(trial):
    # Define hyperparameters to tune
    params = {
        'objective': 'binary',
        'metric': 'binary_logloss',
        'boosting_type': 'gbdt',
        'num_leaves': trial.suggest_int('num_leaves', 2, 256),
        'learning_rate': trial.suggest_float('learning_rate', 0.001, 1.0),
        'feature_fraction': trial.suggest_float('feature_fraction', 0.1, 1.0),
        'bagging_fraction': trial.suggest_float('bagging_fraction', 0.1, 1.0),
        'bagging_freq': trial.suggest_int('bagging_freq', 1, 10),
        'min_child_samples': trial.suggest_int('min_child_samples', 5, 100),
        'device': 'gpu',
        'verbosity': -1
    }
    
    # Define cross-validation parameters
    n_splits = 10
    skf = StratifiedKFold(n_splits=n_splits, shuffle=True, random_state=42)
    
    # Initialize array to store out-of-fold predictions
    oof_preds = np.zeros(train_df.shape[0])
    
    # Loop over each fold and train a model
    for fold, (train_idx, val_idx) in enumerate(skf.split(train_df, train_df['Class'])):
        X_train, y_train = train_df.iloc[train_idx].drop('Class', axis=1), train_df.iloc[train_idx]['Class']
        X_val, y_val = train_df.iloc[val_idx].drop('Class', axis=1), train_df.iloc[val_idx]['Class']
        
        clf = lgb.LGBMClassifier(**params, class_weight= class_weights_lgbm)
        clf.fit(X_train, y_train, eval_set=[(X_val, y_val)])
        
        oof_preds[val_idx] = clf.predict_proba(X_val)[:, 1]
    
    # Calculate log loss
    logloss = log_loss(train_df['Class'], oof_preds)
    
    return logloss


In [15]:
study = optuna.create_study(direction='minimize')
study.optimize(objective, n_trials=100)


[I 2023-05-13 09:16:45,781] A new study created in memory with name: no-name-0c0ee1e5-a364-4341-9d7c-ee8e947b75e8


[LightGBM] [Warning] feature_fraction is set=0.44791912773566733, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.44791912773566733
[LightGBM] [Warning] bagging_fraction is set=0.21007104064307858, subsample=1.0 will be ignored. Current value: bagging_fraction=0.21007104064307858
[LightGBM] [Warning] bagging_freq is set=1, subsample_freq=0 will be ignored. Current value: bagging_freq=1
[1]	valid_0's binary_logloss: 0.874846
[2]	valid_0's binary_logloss: 3.82538
[3]	valid_0's binary_logloss: 4.39962
[4]	valid_0's binary_logloss: 7.80626
[5]	valid_0's binary_logloss: 9.26188
[6]	valid_0's binary_logloss: 13.922
[7]	valid_0's binary_logloss: 14.5058
[8]	valid_0's binary_logloss: 15.2811
[9]	valid_0's binary_logloss: 20.065
[10]	valid_0's binary_logloss: 21.9683
[11]	valid_0's binary_logloss: 26.8169
[12]	valid_0's binary_logloss: 26.8169
[13]	valid_0's binary_logloss: 26.8169
[14]	valid_0's binary_logloss: 26.8169
[15]	valid_0's binary_logloss: 26.8169
[16]	valid_0

[LightGBM] [Warning] feature_fraction is set=0.44791912773566733, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.44791912773566733
[LightGBM] [Warning] bagging_fraction is set=0.21007104064307858, subsample=1.0 will be ignored. Current value: bagging_fraction=0.21007104064307858
[LightGBM] [Warning] bagging_freq is set=1, subsample_freq=0 will be ignored. Current value: bagging_freq=1
[1]	valid_0's binary_logloss: 0.831623
[2]	valid_0's binary_logloss: 6.41704
[3]	valid_0's binary_logloss: 7.0161
[4]	valid_0's binary_logloss: 6.71151
[5]	valid_0's binary_logloss: 7.87697
[6]	valid_0's binary_logloss: 6.33455
[7]	valid_0's binary_logloss: 12.2245
[8]	valid_0's binary_logloss: 16.0086
[9]	valid_0's binary_logloss: 16.769
[10]	valid_0's binary_logloss: 24.9452
[11]	valid_0's binary_logloss: 11.0791
[12]	valid_0's binary_logloss: 28.493
[13]	valid_0's binary_logloss: 4.66902
[14]	valid_0's binary_logloss: 4.66902
[15]	valid_0's binary_logloss: 4.66902
[16]	valid_0'

[96]	valid_0's binary_logloss: 28.5529
[97]	valid_0's binary_logloss: 28.5529
[98]	valid_0's binary_logloss: 28.5529
[99]	valid_0's binary_logloss: 28.5529
[100]	valid_0's binary_logloss: 28.5529
[LightGBM] [Warning] feature_fraction is set=0.44791912773566733, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.44791912773566733
[LightGBM] [Warning] bagging_fraction is set=0.21007104064307858, subsample=1.0 will be ignored. Current value: bagging_fraction=0.21007104064307858
[LightGBM] [Warning] bagging_freq is set=1, subsample_freq=0 will be ignored. Current value: bagging_freq=1
[1]	valid_0's binary_logloss: 0.887959
[2]	valid_0's binary_logloss: 3.8991
[3]	valid_0's binary_logloss: 8.48357
[4]	valid_0's binary_logloss: 6.27055
[5]	valid_0's binary_logloss: 8.71195
[6]	valid_0's binary_logloss: 8.85809
[7]	valid_0's binary_logloss: 14.5291
[8]	valid_0's binary_logloss: 16.8152
[9]	valid_0's binary_logloss: 18.9222
[10]	valid_0's binary_logloss: 19.8716
[11]	valid

[97]	valid_0's binary_logloss: 21.3697
[98]	valid_0's binary_logloss: 21.3697
[99]	valid_0's binary_logloss: 21.3697
[100]	valid_0's binary_logloss: 21.3697
[LightGBM] [Warning] feature_fraction is set=0.44791912773566733, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.44791912773566733
[LightGBM] [Warning] bagging_fraction is set=0.21007104064307858, subsample=1.0 will be ignored. Current value: bagging_fraction=0.21007104064307858
[LightGBM] [Warning] bagging_freq is set=1, subsample_freq=0 will be ignored. Current value: bagging_freq=1
[1]	valid_0's binary_logloss: 0.927323
[2]	valid_0's binary_logloss: 3.59907
[3]	valid_0's binary_logloss: 5.7177
[4]	valid_0's binary_logloss: 8.60949
[5]	valid_0's binary_logloss: 9.40278
[6]	valid_0's binary_logloss: 9.95604
[7]	valid_0's binary_logloss: 13.0144
[8]	valid_0's binary_logloss: 15.8358
[9]	valid_0's binary_logloss: 19.8144
[10]	valid_0's binary_logloss: 22.5837
[11]	valid_0's binary_logloss: 21.2869
[12]	valid

...

[60]	valid_0's binary_logloss: 0.317474
[61]	valid_0's binary_logloss: 0.317964
[62]	valid_0's binary_logloss: 0.318008
[63]	valid_0's binary_logloss: 0.319127
[64]	valid_0's binary_logloss: 0.321251
[65]	valid_0's binary_logloss: 0.324177
[66]	valid_0's binary_logloss: 0.324134
[67]	valid_0's binary_logloss: 0.324528
[68]	valid_0's binary_logloss: 0.325699
[69]	valid_0's binary_logloss: 0.327911
[70]	valid_0's binary_logloss: 0.330401
[71]	valid_0's binary_logloss: 0.333132
[72]	valid_0's binary_logloss: 0.335585
[73]	valid_0's binary_logloss: 0.337111
[74]	valid_0's binary_logloss: 0.339557
[75]	valid_0's binary_logloss: 0.340761
[76]	valid_0's binary_logloss: 0.343277
[77]	valid_0's binary_logloss: 0.345914
[78]	valid_0's binary_logloss: 0.349132
[79]	valid_0's binary_logloss: 0.350778
[80]	valid_0's binary_logloss: 0.35233
[81]	valid_0's binary_logloss: 0.356291
[82]	valid_0's binary_logloss: 0.359123
[83]	valid_0's binary_logloss: 0.361452
[84]	valid_0's binary_logloss: 0.363474
[

[47]	valid_0's binary_logloss: 0.246902
[48]	valid_0's binary_logloss: 0.245065
[49]	valid_0's binary_logloss: 0.245379
[50]	valid_0's binary_logloss: 0.244499
[51]	valid_0's binary_logloss: 0.243412
[52]	valid_0's binary_logloss: 0.242392
[53]	valid_0's binary_logloss: 0.241983
[54]	valid_0's binary_logloss: 0.24334
[55]	valid_0's binary_logloss: 0.241096
[56]	valid_0's binary_logloss: 0.239968
[57]	valid_0's binary_logloss: 0.239553
[58]	valid_0's binary_logloss: 0.241289
[59]	valid_0's binary_logloss: 0.241545
[60]	valid_0's binary_logloss: 0.242146
[61]	valid_0's binary_logloss: 0.24076
[62]	valid_0's binary_logloss: 0.241398
[63]	valid_0's binary_logloss: 0.241582
[64]	valid_0's binary_logloss: 0.242102
[65]	valid_0's binary_logloss: 0.242523
[66]	valid_0's binary_logloss: 0.243606
[67]	valid_0's binary_logloss: 0.242579
[68]	valid_0's binary_logloss: 0.243349
[69]	valid_0's binary_logloss: 0.243955
[70]	valid_0's binary_logloss: 0.244902
[71]	valid_0's binary_logloss: 0.244861
[7

[33]	valid_0's binary_logloss: 0.310441
[34]	valid_0's binary_logloss: 0.305758
[35]	valid_0's binary_logloss: 0.301784
[36]	valid_0's binary_logloss: 0.296714
[37]	valid_0's binary_logloss: 0.29419
[38]	valid_0's binary_logloss: 0.293961
[39]	valid_0's binary_logloss: 0.290996
[40]	valid_0's binary_logloss: 0.289926
[41]	valid_0's binary_logloss: 0.286533
[42]	valid_0's binary_logloss: 0.28545
[43]	valid_0's binary_logloss: 0.285344
[44]	valid_0's binary_logloss: 0.283647
[45]	valid_0's binary_logloss: 0.281984
[46]	valid_0's binary_logloss: 0.28182
[47]	valid_0's binary_logloss: 0.283001
[48]	valid_0's binary_logloss: 0.283229
[49]	valid_0's binary_logloss: 0.283249
[50]	valid_0's binary_logloss: 0.282058
[51]	valid_0's binary_logloss: 0.282444
[52]	valid_0's binary_logloss: 0.281884
[53]	valid_0's binary_logloss: 0.281997
[54]	valid_0's binary_logloss: 0.281345
[55]	valid_0's binary_logloss: 0.282379
[56]	valid_0's binary_logloss: 0.28142
[57]	valid_0's binary_logloss: 0.281944
[58]

[I 2023-05-13 10:10:51,220] Trial 99 finished with value: 0.35565067997219457 and parameters: {'num_leaves': 205, 'learning_rate': 0.10322573490758603, 'feature_fraction': 0.9770756674962082, 'bagging_fraction': 0.9626800136591931, 'bagging_freq': 1, 'min_child_samples': 18}. Best is trial 94 with value: 0.2601469147433728.


[99]	valid_0's binary_logloss: 0.371158
[100]	valid_0's binary_logloss: 0.372802


In [16]:
params = study.best_params

best_lgbm = lgb.LGBMClassifier(**params)


In [18]:
print(params)

{'num_leaves': 242, 'learning_rate': 0.050777443096144514, 'feature_fraction': 0.8926350700255699, 'bagging_fraction': 0.8634760925381602, 'bagging_freq': 1, 'min_child_samples': 8}


# Part 2
---
Cross-Validation with stratifiedShuffleSplit with 10 splits on Catboost with Optuna, the referenced solution for this was done using grid search to get the best hyperparameters for catboost but using it seemed too slow.

In [19]:
#weights for catboost
class_weights_catboost = {0: 1, 1: 100}

In [20]:
def objective1(trial):
    
    # Define the hyperparameter search space
    params = {
        'learning_rate': trial.suggest_float('learning_rate', 0.01, 0.2),
        'depth': trial.suggest_int('depth', 4, 10),
        'l2_leaf_reg': trial.suggest_float('l2_leaf_reg', 1, 10),
        'n_estimators': trial.suggest_int('n_estimators', 100, 400),
        'class_weights': class_weights_catboost
    }
    
    # Create an instance of CatBoostClassifier with the hyperparameters suggested by Optuna
    catboost = CatBoostClassifier(**params, task_type='GPU', verbose=False)
    
    # Use stratified shuffle split cross-validation to evaluate the model
    cv = StratifiedShuffleSplit(n_splits=10, test_size=0.2, random_state=42)
    scores = []
    for train_idx, test_idx in cv.split(X, y):
        X_train, X_test = X.iloc[train_idx], X.iloc[test_idx]
        y_train, y_test = y.iloc[train_idx], y.iloc[test_idx]
        catboost.fit(X_train, y_train)
        score = catboost.score(X_test, y_test)
        scores.append(score)
        
    # Return the average AUC score across all cross-validation folds
    return np.mean(scores)


In [21]:
# Run the hyperparameter search using Optuna
study1 = optuna.create_study(direction='maximize')
study1.optimize(objective1, n_trials=50)

# Print the best hyperparameters and their AUC score
print('Best parameters:', study1.best_params)
print('Best AUC score:', study1.best_value)


catboost_params = study1.best_params

[I 2023-05-13 10:10:51,309] A new study created in memory with name: no-name-1461e653-c7cf-47ab-a79e-5e60c157bfe5
[I 2023-05-13 10:11:31,693] Trial 0 finished with value: 0.9034662045060659 and parameters: {'learning_rate': 0.19132559177232428, 'depth': 8, 'l2_leaf_reg': 2.181781275446392, 'n_estimators': 362}. Best is trial 0 with value: 0.9034662045060659.
[I 2023-05-13 10:11:43,581] Trial 1 finished with value: 0.47461005199306766 and parameters: {'learning_rate': 0.054201562218742616, 'depth': 4, 'l2_leaf_reg': 9.771286858413399, 'n_estimators': 168}. Best is trial 0 with value: 0.9034662045060659.
[I 2023-05-13 10:12:36,088] Trial 2 finished with value: 0.9034662045060659 and parameters: {'learning_rate': 0.09864421758109425, 'depth': 10, 'l2_leaf_reg': 4.062238485022854, 'n_estimators': 247}. Best is trial 0 with value: 0.9034662045060659.
[I 2023-05-13 10:12:58,362] Trial 3 finished with value: 0.8493067590987868 and parameters: {'learning_rate': 0.1598488816862736, 'depth': 6, 

[I 2023-05-13 10:35:00,912] Trial 31 finished with value: 0.911785095320624 and parameters: {'learning_rate': 0.12754843298643376, 'depth': 10, 'l2_leaf_reg': 1.6346887459157313, 'n_estimators': 346}. Best is trial 12 with value: 0.9138648180242634.
[I 2023-05-13 10:36:10,328] Trial 32 finished with value: 0.9111785095320624 and parameters: {'learning_rate': 0.12531475835170533, 'depth': 10, 'l2_leaf_reg': 2.387906887504971, 'n_estimators': 350}. Best is trial 12 with value: 0.9138648180242634.
[I 2023-05-13 10:37:36,419] Trial 33 finished with value: 0.9131715771230502 and parameters: {'learning_rate': 0.11422312229049071, 'depth': 10, 'l2_leaf_reg': 1.5384963428661198, 'n_estimators': 400}. Best is trial 12 with value: 0.9138648180242634.
[I 2023-05-13 10:39:00,737] Trial 34 finished with value: 0.9122183708838822 and parameters: {'learning_rate': 0.1077532906574238, 'depth': 10, 'l2_leaf_reg': 1.7051339124531855, 'n_estimators': 371}. Best is trial 12 with value: 0.9138648180242634.

Best parameters: {'learning_rate': 0.14264515306539477, 'depth': 10, 'l2_leaf_reg': 1.5402079291819863, 'n_estimators': 358}
Best AUC score: 0.9146447140381282


In [22]:
best_catboost = CatBoostClassifier(**catboost_params, task_type='GPU', verbose=False)

# Part 3
---
Oversampling with SMOTE and then cross-validation with kFOLD 10 splits on xgbclassifier hypertuned with Optuna.

In [24]:
# Define the SMOTE oversampling strategy
oversample = SMOTE(sampling_strategy='minority')

# Apply the oversampling strategy to the feature and target data
X_resampled, y_resampled = oversample.fit_resample(X, y)


# Define the objective function for Optuna
def objective2(trial):
    # Define the hyperparameters to optimize
    params = {
        'max_depth': trial.suggest_int('max_depth', 3, 7),
        'learning_rate': trial.suggest_float('learning_rate', 0.001, 1),
        'n_estimators': trial.suggest_int('n_estimators', 50, 200),
       
    }
    
    # Define the XGBClassifier model with the specified hyperparameters
    xgb = XGBClassifier(**params)
    
    # Define the KFold cross-validation object
    cv = KFold(n_splits=10, shuffle=True, random_state=42)
    
    # Calculate the mean cross-validated score using ROC AUC
    scores = cross_val_score(xgb, X_resampled, y_resampled, cv=cv, scoring='roc_auc')
    mean_score = scores.mean()
    
    # Return the mean score as the objective value for Optuna to minimize
    return mean_score


In [25]:
study2 = optuna.create_study(direction='maximize')
study2.optimize(objective2, n_trials=100)

# Print the best hyperparameters found during the search
print("Best Hyperparameters: ", study2.best_params)

# Print the best cross-validated score found during the search
print("CV Score: ", study2.best_value)

xgb_params = study2.best_params

[I 2023-05-13 10:53:31,018] A new study created in memory with name: no-name-2583bca0-6739-4c5f-bc95-09986bc79bc1
[I 2023-05-13 10:53:47,533] Trial 0 finished with value: 0.9907059801124216 and parameters: {'max_depth': 7, 'learning_rate': 0.20950187561170872, 'n_estimators': 131}. Best is trial 0 with value: 0.9907059801124216.
[I 2023-05-13 10:53:56,424] Trial 1 finished with value: 0.9858085491722471 and parameters: {'max_depth': 4, 'learning_rate': 0.7215922442408474, 'n_estimators': 120}. Best is trial 0 with value: 0.9907059801124216.
[I 2023-05-13 10:54:03,870] Trial 2 finished with value: 0.9881963854571877 and parameters: {'max_depth': 6, 'learning_rate': 0.7571128401442421, 'n_estimators': 73}. Best is trial 0 with value: 0.9907059801124216.
[I 2023-05-13 10:54:09,530] Trial 3 finished with value: 0.9841272215475652 and parameters: {'max_depth': 5, 'learning_rate': 0.5450229685995194, 'n_estimators': 59}. Best is trial 0 with value: 0.9907059801124216.
[I 2023-05-13 10:54:16,

[I 2023-05-13 11:02:43,770] Trial 35 finished with value: 0.9917947821592747 and parameters: {'max_depth': 7, 'learning_rate': 0.46399751808175144, 'n_estimators': 194}. Best is trial 22 with value: 0.9919275238400358.
[I 2023-05-13 11:03:01,965] Trial 36 finished with value: 0.9909536946075969 and parameters: {'max_depth': 6, 'learning_rate': 0.31199489209179015, 'n_estimators': 183}. Best is trial 22 with value: 0.9919275238400358.
[I 2023-05-13 11:03:10,880] Trial 37 finished with value: 0.9895457238715372 and parameters: {'max_depth': 7, 'learning_rate': 0.39011769645497296, 'n_estimators': 72}. Best is trial 22 with value: 0.9919275238400358.
[I 2023-05-13 11:03:31,657] Trial 38 finished with value: 0.9900691419720516 and parameters: {'max_depth': 7, 'learning_rate': 0.11306075012072167, 'n_estimators': 162}. Best is trial 22 with value: 0.9919275238400358.
[I 2023-05-13 11:03:43,243] Trial 39 finished with value: 0.9883998060123339 and parameters: {'max_depth': 6, 'learning_rate'

[I 2023-05-13 11:12:37,545] Trial 71 finished with value: 0.9917403308170533 and parameters: {'max_depth': 7, 'learning_rate': 0.2734851579307679, 'n_estimators': 190}. Best is trial 47 with value: 0.9921558547528964.
[I 2023-05-13 11:12:54,943] Trial 72 finished with value: 0.9918038498407528 and parameters: {'max_depth': 7, 'learning_rate': 0.2608401170567775, 'n_estimators': 190}. Best is trial 47 with value: 0.9921558547528964.
[I 2023-05-13 11:13:09,942] Trial 73 finished with value: 0.9918827532402862 and parameters: {'max_depth': 7, 'learning_rate': 0.4032165792215073, 'n_estimators': 185}. Best is trial 47 with value: 0.9921558547528964.
[I 2023-05-13 11:13:25,967] Trial 74 finished with value: 0.9917637228858265 and parameters: {'max_depth': 7, 'learning_rate': 0.28322324029364104, 'n_estimators': 178}. Best is trial 47 with value: 0.9921558547528964.
[I 2023-05-13 11:13:42,635] Trial 75 finished with value: 0.9920669926761821 and parameters: {'max_depth': 7, 'learning_rate': 

Best Hyperparameters:  {'max_depth': 7, 'learning_rate': 0.3430150960074839, 'n_estimators': 200}
CV Score:  0.9921558547528964


In [26]:
best_xgb = XGBClassifier(**xgb_params)

# All together as an ensemble
---
Making an ensemble with all the models.

In [28]:
#Final changes needed to be made to test set

scaler.fit(test_df)
finaltest = scaler.transform(test_df)
finaltest = pd.DataFrame(finaltest, columns=test_df.columns)


In [29]:
best_xgb.fit(X, y)
best_lgbm.fit(X, y)
best_catboost.fit(X, y)

[LightGBM] [Warning] feature_fraction is set=0.8926350700255699, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.8926350700255699
[LightGBM] [Warning] bagging_fraction is set=0.8634760925381602, subsample=1.0 will be ignored. Current value: bagging_fraction=0.8634760925381602
[LightGBM] [Warning] bagging_freq is set=1, subsample_freq=0 will be ignored. Current value: bagging_freq=1


In [30]:
# Define the individual models
xgb = best_xgb
lgbm = best_lgbm
cat = best_catboost

# Define the ensemble model with the individual models
ensemble = VotingClassifier(estimators=[('xgb', xgb),('lgbm', lgbm), ('cat', cat)], voting='soft')

#Taking out xgb due to fuck up and check  

# Train the ensemble model
ensemble.fit(X, y)

# Make predictions with the ensemble model
y_pred = ensemble.predict(finaltest)

In [31]:
# Create a new DataFrame with 'id' and 'Class' columns
submission_df = pd.DataFrame({'id': test['id'], 'Class': y_pred})

# Save the new DataFrame to a CSV file
submission_df.to_csv('submissionrevamp.csv', index=False)

Quick preview of the class predictions made using the ensemble and the models individually.

In [32]:
countsreal = submission_df['Class'].value_counts()
print(countsreal)

0    143925
1      2162
Name: Class, dtype: int64


In [33]:
y_pred_smotexgb = xgb.predict(finaltest)
checkxgb = pd.DataFrame({'id': test['id'], 'Class': y_pred_smotexgb})

In [34]:
counts1 = checkxgb['Class'].value_counts()
print(counts1)

0    142434
1      3653
Name: Class, dtype: int64


In [35]:
y_pred_cb = cat.predict(finaltest)
checkcb = pd.DataFrame({'id': test['id'], 'Class': y_pred_cb})

In [36]:
counts2 = checkcb['Class'].value_counts()
print(counts2)

0    143633
1      2454
Name: Class, dtype: int64


In [37]:
y_pred_lgbm = lgbm.predict(finaltest)
checklgbm = pd.DataFrame({'id': test['id'], 'Class': y_pred_lgbm})

In [38]:
counts3 = checklgbm['Class'].value_counts()
print(counts3)

0    144080
1      2007
Name: Class, dtype: int64


## Final comments
---
The final score of the predictions using the ensemble is not ideal and it could be improved by refining the models' hyperparameters and further feature engineering. Due to time constraints, this was not done but taking the referenced solutions into account, it should be able to achieve a score that is acceptable if not great. 